In [50]:
from dash import Dash, html, dash_table, dcc, callback, Output, Input
import pandas as pd
import plotly.express as px
import yfinance as yf
import dash_bootstrap_components as dbc

In [51]:
# Load data
emissions = pd.read_csv('co2_emissions_kt_by_country.csv')
region = pd.read_csv('Methane_final.csv')
gdp = pd.read_csv('world_country_gdp_usd.csv')
pop = pd.read_csv('population_by_country_2020.csv')

region = region.drop(columns=['Unnamed: 0'])

gdp.columns = gdp.columns.str.replace(' ', '_')
gdp.columns = gdp.columns.str.lower()

pop = pop.rename(columns={'Country (or dependency)': 'country', 'Population (2020)': 'population', 'Density (P/Km²)': 'density', 
                          'Land Area (Km²)': 'land_area', 'Migrants (net)': 'migrants', 'Fert. Rate': 'fert_rate', 'Med. Age': 'med_age', 'Urban Pop %': 'urban_pop'})

In [52]:
pop

country  population Yearly Change  Net Change  density  \
0               China  1440297825        0.39 %     5540090      153   
1               India  1382345085        0.99 %    13586631      464   
2       United States   331341050        0.59 %     1937734       36   
3           Indonesia   274021604        1.07 %     2898047      151   
4            Pakistan   221612785        2.00 %     4327022      287   
..                ...         ...           ...         ...      ...   
230        Montserrat        4993        0.06 %           3       50   
231  Falkland Islands        3497        3.05 %         103        0   
232              Niue        1628        0.68 %          11        6   
233           Tokelau        1360        1.27 %          17      136   
234          Holy See         801        0.25 %           2     2003   

     land_area  migrants fert_rate med_age urban_pop World Share  
0      9388211 -348399.0       1.7      38      61 %     18.47 %  
1      2973190 -532687.0       2.2      28      35 %     17.70 %  
2      9147420  954806.0       1.8      38      83 %      4.25 %  
3      1811570  -98955.0       2.3      30      56 %      3.51 %  
4       770880 -233379.0       3.6      23      35 %      2.83 %  
..         ...       ...       ...     ...       ...         ...  
230        100       NaN      N.A.    N.A.      10 %      0.00 %  
231      12170       NaN      N.A.    N.A.      66 %      0.00 %  
232        260       NaN      N.A.    N.A.      46 %      0.00 %  
233         10       NaN      N.A.    N.A.       0 %      0.00 %  
234          0       NaN      N.A.    N.A.      N.A.      0.00 %  

[235 rows x 11 columns]

In [53]:
# merge emissions and gdp
merge = pd.merge(emissions, gdp, left_on='country_code', right_on='country_code', how='inner')
merge = merge.drop(columns=['country_name_y', 'year_y'])
merge = merge.rename(columns={'country_name_x': 'country_name', 'year_x': 'year'})
sec_merge = pd.merge(merge, region, left_on='country_name', right_on='country', how='inner')
final_merge = pd.merge(sec_merge, pop, left_on='country_name', right_on='country', how='inner')
emissions_gdp = final_merge.copy()


In [54]:
emissions_gdp = emissions_gdp.drop(columns=['country_x', 'type', 'segment', 'reason', 'baseYear', 'notes'])
emissions_gdp = emissions_gdp.rename(columns={'country_name': 'country', 'value': 'co2_emissions', 'gdp_usd': 'gdp', 'gdp_per_capita_usd':'gdp_per_capita', 'emissions':'methane_emissions'})

emissions_gdp_2018 = emissions_gdp[emissions_gdp['year'] == 2018]

In [55]:
emissions_gdp

country_code       country  year  co2_emissions           gdp  \
0                AGO        Angola  1960     550.050000           NaN   
1                AGO        Angola  1960     550.050000           NaN   
2                AGO        Angola  1960     550.050000           NaN   
3                AGO        Angola  1960     550.050000           NaN   
4                AGO        Angola  1960     550.050000           NaN   
...              ...           ...   ...            ...           ...   
4249785          ZAF  South Africa  2019  439640.014648  4.199460e+11   
4249786          ZAF  South Africa  2019  439640.014648  4.199460e+11   
4249787          ZAF  South Africa  2019  439640.014648  4.199460e+11   
4249788          ZAF  South Africa  2019  439640.014648  4.199460e+11   
4249789          ZAF  South Africa  2019  439640.014648  4.199460e+11   

         gdp_per_capita  region  methane_emissions     country_y  population  \
0                   NaN  Africa         400.969574        Angola    33032075   
1                   NaN  Africa          57.340000        Angola    33032075   
2                   NaN  Africa           2.591680        Angola    33032075   
3                   NaN  Africa           1.381880        Angola    33032075   
4                   NaN  Africa          47.643501        Angola    33032075   
...                 ...     ...                ...           ...         ...   
4249785     6994.211654  Africa          10.874123  South Africa    59436725   
4249786     6994.211654  Africa        1060.310059  South Africa    59436725   
4249787     6994.211654  Africa        1239.029663  South Africa    59436725   
4249788     6994.211654  Africa          42.407463  South Africa    59436725   
4249789     6994.211654  Africa         834.214050  South Africa    59436725   

        Yearly Change  Net Change  density  land_area  migrants fert_rate  \
0              3.27 %     1040977       26    1246700    6413.0       5.6   
1              3.27 %     1040977       26    1246700    6413.0       5.6   
2              3.27 %     1040977       26    1246700    6413.0       5.6   
3              3.27 %     1040977       26    1246700    6413.0       5.6   
4              3.27 %     1040977       26    1246700    6413.0       5.6   
...               ...         ...      ...        ...       ...       ...   
4249785        1.28 %      750420       49    1213090  145405.0       2.4   
4249786        1.28 %      750420       49    1213090  145405.0       2.4   
4249787        1.28 %      750420       49    1213090  145405.0       2.4   
4249788        1.28 %      750420       49    1213090  145405.0       2.4   
4249789        1.28 %      750420       49    1213090  145405.0       2.4   

        med_age urban_pop World Share  
0            17      67 %      0.42 %  
1            17      67 %      0.42 %  
2            17      67 %      0.42 %  
3            17      67 %      0.42 %  
4            17      67 %      0.42 %  
...         ...       ...         ...  
4249785      28      67 %      0.76 %  
4249786      28      67 %      0.76 %  
4249787      28      67 %      0.76 %  
4249788      28      67 %      0.76 %  
4249789      28      67 %      0.76 %  

[4249790 rows x 19 columns]

In [56]:
px.histogram(emissions_gdp_2018, x='region', y='gdp')

In [58]:
hist_data = emissions_gdp_2018[emissions_gdp_2018['co2_emissions'] > 200000]

px.histogram(hist_data, x='country', y='co2_emissions')